In [1]:
from transformers import AutoModel, AutoTokenizer
from pycocotools.coco import COCO
from pycocoevalcap.eval import COCOEvalCap
from huggingface_hub import login
import torch
import os
import json
from PIL import Image
from tqdm import tqdm
import numpy as np
import math
import torchvision.transforms as T
from torchvision.transforms.functional import InterpolationMode

/home/kezouke/Thesis/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/kezouke/Thesis/.venv/lib/python3.12/site-packages/torch/cuda/__init__.py:63: FutureWarning: The pynvml package is deprecated. Please install nvidia-ml-py instead. If you did not install pynvml directly, please report this to the maintainers of the package that installed pynvml for you.
  import pynvml  # type: ignore[import]


In [ ]:
your_hf_token = ""
login(token=your_hf_token)

In [ ]:
# Configuration
MODEL_PATH = "OpenGVLab/InternVL3_5-8B"
COCO_DIR = "Thesis/coco2014"
IMAGE_DIR = os.path.join(COCO_DIR, "val2014")
ANNOTATION_FILE = os.path.join(COCO_DIR, "annotations", "captions_val2014.json")
OUTPUT_FILE = "internvl3_5_8b_coco_results_val.json"
BATCH_SIZE = 2  # Smaller batch size due to high memory usage
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"

# Generation parameters
GENERATION_CONFIG = {
    "max_new_tokens": 50,
    "do_sample": False,  # Use greedy decoding for consistency
}

# Image processing constants
IMAGENET_MEAN = (0.485, 0.456, 0.406)
IMAGENET_STD = (0.229, 0.224, 0.225)
IMAGE_SIZE = 448  # InternVL uses 448x448 resolution


In [4]:
torch.cuda.empty_cache()
if torch.cuda.is_available():
    print(f"Free GPU memory: {torch.cuda.mem_get_info()[0] / 1024**3:.2f} GB")

Free GPU memory: 23.30 GB


In [5]:
def build_transform(input_size):
    """Build image transform for InternVL."""
    MEAN, STD = IMAGENET_MEAN, IMAGENET_STD
    transform = T.Compose([
        T.Lambda(lambda img: img.convert('RGB') if img.mode != 'RGB' else img),
        T.Resize((input_size, input_size), interpolation=InterpolationMode.BICUBIC),
        T.ToTensor(),
        T.Normalize(mean=MEAN, std=STD)
    ])
    return transform

def find_closest_aspect_ratio(aspect_ratio, target_ratios, width, height, image_size):
    """Find closest aspect ratio for dynamic preprocessing."""
    best_ratio_diff = float('inf')
    best_ratio = (1, 1)
    area = width * height
    for ratio in target_ratios:
        target_aspect_ratio = ratio[0] / ratio[1]
        ratio_diff = abs(aspect_ratio - target_aspect_ratio)
        if ratio_diff < best_ratio_diff:
            best_ratio_diff = ratio_diff
            best_ratio = ratio
        elif ratio_diff == best_ratio_diff:
            if area > 0.5 * image_size * image_size * ratio[0] * ratio[1]:
                best_ratio = ratio
    return best_ratio

def dynamic_preprocess(image, min_num=1, max_num=12, image_size=448, use_thumbnail=False):
    """Dynamic preprocessing for InternVL."""
    orig_width, orig_height = image.size
    aspect_ratio = orig_width / orig_height

    # Calculate target ratios
    target_ratios = set(
        (i, j) for n in range(min_num, max_num + 1) 
        for i in range(1, n + 1) 
        for j in range(1, n + 1) 
        if i * j <= max_num and i * j >= min_num
    )
    target_ratios = sorted(target_ratios, key=lambda x: x[0] * x[1])

    # Find closest aspect ratio
    target_aspect_ratio = find_closest_aspect_ratio(
        aspect_ratio, target_ratios, orig_width, orig_height, image_size
    )

    # Calculate target dimensions
    target_width = image_size * target_aspect_ratio[0]
    target_height = image_size * target_aspect_ratio[1]
    blocks = target_aspect_ratio[0] * target_aspect_ratio[1]

    # Resize image
    resized_img = image.resize((target_width, target_height))
    processed_images = []
    
    # Split image into tiles
    for i in range(blocks):
        box = (
            (i % (target_width // image_size)) * image_size,
            (i // (target_width // image_size)) * image_size,
            ((i % (target_width // image_size)) + 1) * image_size,
            ((i // (target_width // image_size)) + 1) * image_size
        )
        split_img = resized_img.crop(box)
        processed_images.append(split_img)
    
    assert len(processed_images) == blocks
    
    # Add thumbnail if needed
    if use_thumbnail and len(processed_images) != 1:
        thumbnail_img = image.resize((image_size, image_size))
        processed_images.append(thumbnail_img)
    
    return processed_images

def load_image_for_internvl(image_path, max_num=12):
    """Load and preprocess image for InternVL, returning pixel values and num patches."""
    try:
        image = Image.open(image_path).convert('RGB')
    except Exception as e:
        print(f"Error loading image {image_path}: {e}")
        # Create a blank image as fallback
        image = Image.new('RGB', (IMAGE_SIZE, IMAGE_SIZE), (255, 255, 255))
    
    transform = build_transform(input_size=IMAGE_SIZE)
    images = dynamic_preprocess(
        image, 
        image_size=IMAGE_SIZE, 
        use_thumbnail=True, 
        max_num=max_num
    )
    
    pixel_values = [transform(img) for img in images]
    pixel_values = torch.stack(pixel_values)
    num_patches = pixel_values.size(0)
    
    return pixel_values, num_patches

def load_batch_images(image_paths, max_num=12):
    """
    Load and preprocess a batch of images for InternVL.
    
    Returns:
        pixel_values_batch: Tensor of shape [total_patches, C, H, W]
        num_patches_list: List of number of patches per image
    """
    all_pixel_values = []
    num_patches_list = []
    
    for img_path in image_paths:
        try:
            pixel_values, num_patches = load_image_for_internvl(img_path, max_num)
            all_pixel_values.append(pixel_values)
            num_patches_list.append(num_patches)
        except Exception as e:
            print(f"Error loading batch image {img_path}: {e}")
            # Create fallback blank image
            blank_img = Image.new('RGB', (IMAGE_SIZE, IMAGE_SIZE), (255, 255, 255))
            transform = build_transform(input_size=IMAGE_SIZE)
            pixel_values = transform(blank_img).unsqueeze(0)
            all_pixel_values.append(pixel_values)
            num_patches_list.append(1)
    
    # Concatenate all pixel values into one tensor
    pixel_values_batch = torch.cat(all_pixel_values, dim=0)
    return pixel_values_batch, num_patches_list

def load_model_and_tokenizer(model_path, device):
    """Load InternVL3.5-8B model and tokenizer."""
    print(f"Loading model: {model_path}")
    
    # Load model with optimized settings
    model = AutoModel.from_pretrained(
        model_path,
        torch_dtype=torch.bfloat16,
        low_cpu_mem_usage=True,
        use_flash_attn=True,
        trust_remote_code=True,
        device_map="auto"
    ).eval()
    
    # Load tokenizer
    tokenizer = AutoTokenizer.from_pretrained(
        model_path, 
        trust_remote_code=True, 
        use_fast=False
    )
    
    print(f"✓ Model loaded successfully on {next(model.parameters()).device}")
    return model, tokenizer

def generate_captions_batch_real(image_paths, model, tokenizer, generation_config):
    """
    Generate captions for a batch of images using real batch processing with InternVL3.5-8B.
    
    Args:
        image_paths: List of image file paths
        model: InternVL model
        tokenizer: Tokenizer
        generation_config: Generation configuration
        
    Returns:
        List of generated captions
    """
    try:
        # Load and preprocess all images in the batch
        pixel_values_batch, num_patches_list = load_batch_images(image_paths, max_num=12)
        
        # Move to device
        device = next(model.parameters()).device
        pixel_values_batch = pixel_values_batch.to(device, dtype=torch.bfloat16)
        
        # Create batch questions - one per image
        questions = ['<image>\nGenerate a detailed caption for this image in one sentence.'] * len(image_paths)
        
        # Use batch_chat for true parallel processing
        responses = model.batch_chat(
            tokenizer,
            pixel_values_batch,
            questions=questions,
            generation_config=generation_config,
            num_patches_list=num_patches_list,
            history=None,
            return_history=False
        )
        
        # Clean up responses
        captions = [response.strip() for response in responses]
        return captions
        
    except Exception as e:
        print(f"Error in batch generation: {e}")
        # Fallback to sequential processing if batch fails
        print("Falling back to sequential processing...")
        captions = []
        for img_path in image_paths:
            try:
                pixel_values, _ = load_image_for_internvl(img_path, max_num=12)
                caption = model.chat(
                    tokenizer,
                    pixel_values.to(next(model.parameters()).device, dtype=torch.bfloat16),
                    '<image>\nGenerate a detailed caption for this image in one sentence.',
                    generation_config=generation_config
                )
                captions.append(caption.strip())
            except Exception as e2:
                print(f"Error processing individual image {img_path}: {e2}")
                captions.append("Error generating caption")
        return captions

def evaluate_coco(annotation_file, results_file):
    """Evaluate results using pycocoevalcap."""
    print("\n" + "="*60)
    print("COCO Evaluation Results")
    print("="*60)
    
    # Load COCO API
    coco = COCO(annotation_file)
    coco_results = coco.loadRes(results_file)
    
    # Create evaluator
    coco_eval = COCOEvalCap(coco, coco_results)
    
    # Run evaluation
    coco_eval.evaluate()
    
    # Print scores
    print("\nMetrics:")
    for metric, score in coco_eval.eval.items():
        print(f"  {metric:10s}: {score:.4f}")
    
    return coco_eval.eval

def to_serializable(obj):
    """Convert numpy types to Python natives for JSON serialization."""
    if isinstance(obj, np.generic):
        return obj.item()
    raise TypeError(f"Type {type(obj)} not serializable")

In [6]:
model, tokenizer = load_model_and_tokenizer(MODEL_PATH, DEVICE)

Loading model: OpenGVLab/InternVL3_5-8B


`torch_dtype` is deprecated! Use `dtype` instead!
/home/kezouke/Thesis/.venv/lib/python3.12/site-packages/pydantic/_internal/_generate_schema.py:2249: UnsupportedFieldAttributeWarning: The 'repr' attribute with value False was provided to the `Field()` function, which has no effect in the context it was used. 'repr' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assignment. This may have happened because an `Annotated` type alias using the `type` statement was used, or if the `Field()` function was attached to a single member of a union type.
  warnings.warn(
/home/kezouke/Thesis/.venv/lib/python3.12/site-packages/pydantic/_internal/_generate_schema.py:2249: UnsupportedFieldAttributeWarning: The 'frozen' attribute with value True was provided to the `Field()` function, which has no effect in the context it was used. 'frozen' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assi

FlashAttention2 is not installed.


Loading checkpoint shards: 100%|██████████| 4/4 [01:54<00:00, 28.74s/it]


✓ Model loaded successfully on cuda:0


In [7]:
print(f"\nLoading COCO annotations from {ANNOTATION_FILE}")
coco = COCO(ANNOTATION_FILE)
img_ids = coco.getImgIds()
print(f"Total images: {len(img_ids)}")

# Prepare image data
image_data_list = []
for img_id in img_ids:
    img_info = coco.loadImgs(img_id)[0]
    image_path = os.path.join(IMAGE_DIR, img_info['file_name'])
    if os.path.exists(image_path):
        image_data_list.append((img_id, image_path))
    else:
        print(f"Warning: Image not found at {image_path}")

print(f"Valid images found: {len(image_data_list)}")
print(f"Generating captions for {len(image_data_list)} images...")
print(f"Batch size: {BATCH_SIZE}\n")


Loading COCO annotations from /home/kezouke/Thesis/coco2014/annotations/captions_val2014.json
loading annotations into memory...
Done (t=0.51s)
creating index...
index created!
Total images: 40504
Valid images found: 40504
Generating captions for 40504 images...
Batch size: 2



In [8]:
print("Testing on first batch with real batching...")
test_batch_size = min(BATCH_SIZE, len(image_data_list))
test_batch_data = image_data_list[:test_batch_size]
test_img_ids = [x[0] for x in test_batch_data]
test_paths = [x[1] for x in test_batch_data]

test_captions = generate_captions_batch_real(
    test_paths, 
    model, 
    tokenizer, 
    GENERATION_CONFIG
)

print(f"Sample captions from first batch (real batching):")
for i, (img_id, caption) in enumerate(zip(test_img_ids, test_captions[:3])):
    print(f"  Image ID {img_id}: {caption}")

Testing on first batch with real batching...


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Error in batch generation: CUDA out of memory. Tried to allocate 2.74 GiB. GPU 0 has a total capacity of 23.57 GiB of which 2.45 GiB is free. Including non-PyTorch memory, this process has 21.10 GiB memory in use. Of the allocated memory 20.38 GiB is allocated by PyTorch, and 426.39 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)
Falling back to sequential processing...


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Sample captions from first batch (real batching):
  Image ID 391895: A person wearing a red shirt and helmet rides a motorcycle on a dirt road with a bridge and lush green mountains in the background.
  Image ID 522418: A person wearing a hairnet and red shirt is cutting a large white cake on a table in a kitchen.


In [9]:
BATCH_SIZE = 1

In [10]:
# Process all images in true batches
results = []

for batch_idx in tqdm(range(0, len(image_data_list), BATCH_SIZE), desc="Processing batches"):
    batch_data = image_data_list[batch_idx:batch_idx+BATCH_SIZE]
    img_ids_batch = [x[0] for x in batch_data]
    paths_batch = [x[1] for x in batch_data]
    
    # Generate captions for the entire batch at once
    captions = generate_captions_batch_real(
        paths_batch, 
        model, 
        tokenizer,
        GENERATION_CONFIG
    )
    
    # Add to results
    for img_id, caption in zip(img_ids_batch, captions):
        results.append({
            "image_id": img_id,
            "caption": caption
        })
    
    # Clear GPU cache periodically to prevent memory issues
    if batch_idx % (BATCH_SIZE * 5) == 0:
        torch.cuda.empty_cache()
        if torch.cuda.is_available():
            print(f"GPU memory after cleanup: {torch.cuda.mem_get_info()[0] / 1024**3:.2f} GB free")

Processing batches:   0%|          | 1/40504 [00:01<12:12:32,  1.09s/it]

GPU memory after cleanup: 7.32 GB free


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
Processing batches:   0%|          | 6/40504 [00:10<19:04:12,  1.70s/it]

GPU memory after cleanup: 7.32 GB free


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
Processing batches:   0%|          | 11/40504 [00:21<25:28:26,  2.26s/it]

...

Processing batches: 100%|█████████▉| 40496/40504 [21:58:58<00:15,  1.89s/it]

GPU memory after cleanup: 7.32 GB free


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
Processing batches: 100%|█████████▉| 40501/40504 [21:59:10<00:06,  2.17s/it]

GPU memory after cleanup: 7.32 GB free


Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
Processing batches: 100%|██████████| 40504/40504 [21:59:17<00:00,  1.95s/it]


In [11]:
print(f"\nSaving results to {OUTPUT_FILE}")
with open(OUTPUT_FILE, 'w') as f:
    json.dump(results, f, indent=2)
print("✓ Results saved")


Saving results to internvl3_5_8b_coco_results_val.json
✓ Results saved


In [12]:
# Evaluate with COCO metrics
eval_scores = evaluate_coco(ANNOTATION_FILE, OUTPUT_FILE)

# Save scores
scores_file = OUTPUT_FILE.replace('.json', '_scores.json')
with open(scores_file, 'w') as f:
    json.dump(eval_scores, f, indent=2, default=to_serializable)


COCO Evaluation Results
loading annotations into memory...
Done (t=0.12s)
creating index...
index created!
Loading and preparing results...
DONE (t=0.03s)
creating index...
index created!
tokenization...


PTBTokenizer tokenized 2492309 tokens at 2465172.40 tokens per second.
Nov 30, 2025 10:07:04 PM edu.stanford.nlp.process.PTBLexer next
PTBTokenizer tokenized 969687 tokens at 1906719.77 tokens per second.


setting up scorers...
clipscore is using cuda
computing Bleu score...
{'testlen': 840977, 'reflen': 525728, 'guess': [840977, 800473, 759969, 719465], 'correct': [435385, 198334, 80935, 31568]}
ratio: 1.5996427810578822
Bleu_1: 0.518
Bleu_2: 0.358
Bleu_3: 0.239
Bleu_4: 0.156
computing METEOR score...
METEOR: 0.275
computing Rouge score...
ROUGE_L: 0.450
computing CIDEr score...
CIDEr: 0.327
computing SPICE score...


Parsing reference captions
Parsing test captions


SPICE evaluation took: 30.76 s
SPICE: 0.228
computing CLIPScore score...


...

due to a numerical instability, new numpy normalization is slightly different than paper results. to exactly replicate paper results, please use numpy version less than 1.21, e.g., 1.20.3.


100%|██████████| 792/792 [00:38<00:00, 20.82it/s]


due to a numerical instability, new numpy normalization is slightly different than paper results. to exactly replicate paper results, please use numpy version less than 1.21, e.g., 1.20.3.


40504it [00:00, 122071.18it/s]


CLIPScore: 0.839
RefCLIPScore: 0.812

Metrics:
  Bleu_1    : 0.5177
  Bleu_2    : 0.3582
  Bleu_3    : 0.2391
  Bleu_4    : 0.1565
  METEOR    : 0.2752
  ROUGE_L   : 0.4505
  CIDEr     : 0.3266
  SPICE     : 0.2282
  CLIPScore : 0.8394
  RefCLIPScore: 0.8115
